<a href="https://colab.research.google.com/github/simonsny/image_background_removal/blob/main/bg_removal_workflow.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Connecting to the Google Drive

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# Importing Libraries
import os

import cv2 as cv
import numpy as np
import torch
import torch.nn
from torchvision import transforms
from tqdm import tqdm

Get the Binary Mask with U2Net

In [ ]:
# clone the repository
%cd /content/drive/MyDrive/BeCode/Faktion/
if not os.path.exists('U-2-Net'):
  !git clone https://github.com/NathanUA/U-2-Net.git
%cd U-2-Net
#!python u2net_test.py

[Errno 2] No such file or directory: '/content/drive/MyDrive/BeCode/Faktion/'
/content
Cloning into 'U-2-Net'...
remote: Enumerating objects: 800, done.
remote: Counting objects: 100% (196/196), done.
remote: Compressing objects: 100% (99/99), done.
remote: Total 800 (delta 114), reused 158 (delta 95), pack-reused 604
Receiving objects: 100% (800/800), 30.71 MiB | 16.95 MiB/s, done.
Resolving deltas: 100% (360/360), done.
/content/U-2-Net


Getting the inference from U2Net to get the mask.

In [ ]:
from skimage import io, transform
import torchvision
from torch.autograd import Variable
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms#, utils
# import torch.optim as optim

import numpy as np
from PIL import Image
import glob

from data_loader import RescaleT
from data_loader import ToTensor
from data_loader import ToTensorLab
from data_loader import SalObjDataset

from model import U2NET # full size version 173.6 MB
from model import U2NETP # small version u2net 4.7 MB

# normalize the predicted SOD probability map
def normPRED(d):
    ma = torch.max(d)
    mi = torch.min(d)

    dn = (d-mi)/(ma-mi)

    return dn

def save_output(image_name,pred,d_dir):

    predict = pred
    predict = predict.squeeze()
    predict_np = predict.cpu().data.numpy()

    im = Image.fromarray(predict_np*255).convert('RGB')
    img_name = image_name.split(os.sep)[-1]
    image = io.imread(image_name)
    imo = im.resize((image.shape[1],image.shape[0]),resample=Image.BILINEAR)

    pb_np = np.array(imo)

    aaa = img_name.split(".")
    bbb = aaa[0:-1]
    imidx = bbb[0]
    for i in range(1,len(bbb)):
        imidx = imidx + "." + bbb[i]

    imo.save(d_dir+imidx+'.png')

def main():

    # --------- 1. get image path and name ---------
    model_name='u2net'#u2netp



    image_dir = os.path.join(os.getcwd(), 'test_data', 'test_images')
    prediction_dir = os.path.join(os.getcwd(), 'test_data', model_name + '_results' + os.sep)
    model_dir = os.path.join(os.getcwd(), 'saved_models', model_name, model_name + '.pth')

    img_name_list = glob.glob(image_dir + os.sep + '*')
    print(img_name_list)

    # --------- 2. dataloader ---------
    #1. dataloader
    test_salobj_dataset = SalObjDataset(img_name_list = img_name_list,
                                        lbl_name_list = [],
                                        transform=transforms.Compose([RescaleT(320),
                                                                      ToTensorLab(flag=0)])
                                        )
    test_salobj_dataloader = DataLoader(test_salobj_dataset,
                                        batch_size=1,
                                        shuffle=False,
                                        num_workers=1)

    # --------- 3. model define ---------
    if(model_name=='u2net'):
        print("...load U2NET---173.6 MB")
        net = U2NET(3,1)
    elif(model_name=='u2netp'):
        print("...load U2NEP---4.7 MB")
        net = U2NETP(3,1)

    if torch.cuda.is_available():
        net.load_state_dict(torch.load(model_dir))
        net.cuda()
    else:
        net.load_state_dict(torch.load(model_dir, map_location='cpu'))
    net.eval()

    # --------- 4. inference for each image ---------
    for i_test, data_test in enumerate(test_salobj_dataloader):

        print("inferencing:",img_name_list[i_test].split(os.sep)[-1])

        inputs_test = data_test['image']
        inputs_test = inputs_test.type(torch.FloatTensor)

        if torch.cuda.is_available():
            inputs_test = Variable(inputs_test.cuda())
        else:
            inputs_test = Variable(inputs_test)

        d1,d2,d3,d4,d5,d6,d7= net(inputs_test)

        # normalization
        pred = d1[:,0,:,:]
        pred = normPRED(pred)

        # save results to test_results folder
        if not os.path.exists(prediction_dir):
            os.makedirs(prediction_dir, exist_ok=True)
        save_output(img_name_list[i_test],pred,prediction_dir)

        del d1,d2,d3,d4,d5,d6,d7

if __name__ == "__main__":
    main()

Generate the Trimap from the Binary Mask

In [ ]:
def generate_trimap(mask_path, open_size=10, mask_margin=10):
    """
    Function that loads a mask and generates a trimap and saves it.
    Returns the name of the image.
    """
    mask = cv2.imread(mask_path, 0)

    # make sure if the alpha_matte array has 2 dimensions 
    assert mask.ndim == 2

    # compute each region
    ## get foreground region
    foreground = ((255 - mask_margin) < mask)

    ## get background region
    background = (mask < mask_margin)

    ## get unknown region: outside of background and foreground
    unknown = ~(foreground + background)

    ## dilate unknown area with elliptical kernel.
    unknown = cv2.dilate(
        unknown.astype(np.uint8),
        cv2.getStructuringElement(cv2.MORPH_ELLIPSE, (open_size, open_size))
    ).astype(np.bool)

    # draw trimap
    trimap = np.zeros_like(mask)
    trimap[foreground] = 255
    trimap[unknown] = 127

    # save trimap
    #cv2.imwrite(dst_path, trimap)
    cv2.imwrite(f"/content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Trimap-Output/{mask_path.split('/')[-1]}",trimap)
    return mask_path.split('/')[-1]

In [ ]:
import cv2

mask_path = "/content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Mask/"

for file in os.listdir(mask_path):
  print(file)
  generate_trimap(mask_path + file)
print('done')


Streaming output truncated to the last 5000 lines.
sun_bepuhmvovwnswxep.png
sun_ayaructrdxsdqwbk.png
sun_bcrkfmndsfqahbis.png
sun_awzhyhhhkgakoxjc.png
sun_bdeyhgracifsswoo.png
sun_bxlyrixyuukonwuj.png
sun_bycsfdyqiurvjyer.png
sun_bqtvxgnvpnhvmcmd.png
sun_axuhvcmwmykfnokf.png
sun_bldovaennorwecnn.png
sun_atssirajmpoiljcg.png
sun_asrfdsnqcchmjfmp.png
sun_byoahbcsqdlteagk.png
sun_birvjbwzicvaqkeu.png
sun_bruegippndskcujm.png
sun_axesbqjacwoxtwrj.png
sun_bfweermgnkfuhcnl.png
sun_aztiqzjslyzgkggf.png
sun_atidnlpjhkbfkxxj.png
sun_dxszhpaeqoqzbvtq.png
sun_azhymcpjxzzvsutx.png
sun_aupypzsgthpuxhdb.png
sun_auxrjwofgbjrtcew.png
sun_bgoyalzcawgxodbm.png
sun_bbjvppzxolueahle.png
sun_dhghiusvlrersska.png
sun_bhkcpzeftqjznseu.png
sun_ascplccjyoysqxpt.png
sun_avtzojvejdwsllva.png
sun_bsnfyjkjhldwgosz.png
sun_bonicrtorseimzvs.png
sun_bknbpouuttcmnkku.png
sun_ateurlwwlfrcauct.png
sun_ckhkdzmhpitbkdkc.png
sun_aqzdmsprthcrejfz.png
sun_atgdmqxjostkyken.png
sun_aptkhklljrfbaavj.png
sun_bxxvlyabnxefyhqq.png

Inference with DIM pretrained model

In [ ]:
from torchvision import transforms
%cd /content/drive/MyDrive/BeCode/Faktion/model_code
from config import device
from utils import ensure_folder


IMG_FOLDER = '/content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Image'
TRIMAP_FOLDER ='/content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Trimap-Output'
OUTPUT_FOLDER = '/content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Output'

checkpoint = '/content/drive/MyDrive/BeCode/Faktion/BEST_checkpoint.tar'
checkpoint = torch.load(checkpoint)
model = checkpoint['model'].module
model = model.to(device)
model.eval()


files = [f for f in os.listdir(IMG_FOLDER)]

for file in tqdm(files):
  filename = os.path.join(IMG_FOLDER, file)
  img = cv.imread(filename)
  print(img.shape)
  h, w = img.shape[:2]

  x = torch.zeros((1, 4, h, w), dtype=torch.float)
  image = img[..., ::-1]  # RGB
  image = transforms.ToPILImage()(image)

  transformer = transforms.Compose(
      [
        transforms.ToTensor(),
        transforms.Normalize([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
  ])

  image = transformer(image)
  x[0:, 0:3, :, :] = image


  filename = os.path.join(TRIMAP_FOLDER, file.replace('.jpg', '.png'))
  print('reading {}...'.format(filename))
  trimap = cv.imread(filename, 0)
  print(trimap)
  x[0:, 3, :, :] = torch.from_numpy(trimap.copy() / 255.)
  # print(torch.max(x[0:, 3, :, :]))
  # print(torch.min(x[0:, 3, :, :]))
  # print(torch.median(x[0:, 3, :, :]))

  # Move to GPU, if available
  x = x.type(torch.FloatTensor).to(device)

  with torch.no_grad():
    pred = model(x)

  pred = pred.cpu().numpy()
  pred = pred.reshape((h, w))

  pred[trimap == 0] = 0.0
  pred[trimap == 255] = 1.0

  out = (pred.copy() * 255).astype(np.uint8)

  filename = os.path.join(OUTPUT_FOLDER, file)
  cv.imread(filename)
  cv.imwrite(filename, out)
  print('wrote {}.'.format(filename))

/content/drive/.shortcut-targets-by-id/1pbfU2Nkn_OKUrAgN_cnPqhS91KoSQBr8/Faktion/model_code
1


/usr/local/lib/python3.7/dist-packages/torch/serialization.py:656: SourceChangeWarning: source code of class 'torch.nn.parallel.data_parallel.DataParallel' has changed. you can retrieve the original source code by accessing the object's source attribute or set `torch.nn.Module.dump_patches = True` and use the patch tool to revert the changes.
  warnings.warn(msg, SourceChangeWarning)
/usr/local/lib/python3.7/dist-packages/torch/serialization.py:656: SourceChangeWarning: source code of class 'torch.nn.modules.container.Sequential' has changed. you can retrieve the original source code by accessing the object's source attribute or set `torch.nn.Module.dump_patches = True` and use the patch tool to revert the changes.
  warnings.warn(msg, SourceChangeWarning)
/usr/local/lib/python3.7/dist-packages/torch/serialization.py:656: SourceChangeWarning: source code of class 'torch.nn.modules.conv.Conv2d' has changed. you can retrieve the original source code by accessing the object's source attri

2
model eval
for loop 1
(267, 400, 3)
for loop 2
reading /content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Trimap-Output/sun_aqfwslazedzuwxay.png...
[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]


  0%|          | 1/5019 [00:00<14:54,  5.61it/s]

wrote /content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Output/sun_aqfwslazedzuwxay.jpg.
for loop 1


...

wrote /content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Output/ILSVRC2012_test_00000386.jpg.
for loop 1


100%|█████████▉| 5018/5019 [33:31<00:00,  2.55it/s]

(300, 400, 3)
for loop 2
reading /content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Trimap-Output/ILSVRC2012_test_00000262.png...
[[  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 [  0   0   0 ...   0   0   0]
 ...
 [255 255 255 ...   0   0   0]
 [255 255 255 ...   0   0   0]
 [255 255 255 ...   0   0   0]]
wrote /content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Output/ILSVRC2012_test_00000262.jpg.
for loop 1


100%|██████████| 5019/5019 [33:31<00:00,  2.49it/s]

(308, 400, 3)
for loop 2
reading /content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Trimap-Output/ILSVRC2012_test_00000131.png...
[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
wrote /content/drive/MyDrive/BeCode/Faktion/Datasets/DUTS-TE/DUTS-TE-Output/ILSVRC2012_test_00000131.jpg.
